<img src="ipcc.jpg" width=700 alt="IPCC"></img>

# Cambio Climático: Ensambles multimodelo

---

## Introducción
En este cuadernillo (Notebook) aprenderemos:

1. Breve introduccion a los escenarios de Cambio Climático
1. Proyecto de inter-comparación de modelos de clima acoplados - CMIP
1. Acceso a los datos CMIP6 en formato Zarr
1. Cálculo de la temperatura media global ponderada
1. Reproduccion de la gráfica de la Temperatura Media Global de la Superficie del Mar - CMIP6

## Prerequisitos

| Conceptos | Importancia | Notas |
| --- | --- | --- |
| [Xarray](https://foundations.projectpythia.org/core/xarray.html) | Necesario |  Manejo de datos multidimensionales espacializados|
| [Matplotlib](https://foundations.projectpythia.org/core/matplotlib.html) | Necesario |  Generación de gráficas|
| [CMIP6](https://projectpythia.org/cmip6-cookbook/README.html#) | Necesario |  Ejemplos y analisis de CMIP6|
| [NetCDF](https://foundations.projectpythia.org/core/data-formats/netcdf-cf.html) | Útil | Familiaridad con la estructura de datos y metadatos. |
| [Intake](https://projectpythia.org/intake-cookbook/README.html) | Útil | Cátalogo que nos permite acceder a datos de diversas fuentes |


- **Tiempo de aprendizaje**: 30 minutos.

---

## Librerias

In [1]:
import xarray as xr
import numpy as np
import matplotlib.pyplot as plt

from xmip.preprocessing import combined_preprocessing
from xmip.utils import google_cmip_col

from xarrayutils.plotting import shaded_line_plot
xr.set_options(keep_attrs=True)
%matplotlib inline
%config InlineBackend.figure_format='retina'
plt.rcParams['figure.figsize'] = (10,5)

## 1. Introduccion a los escenarios de Cambio Climático

Los escenarios de cambio climático son una serie de modelos que 

## 2. Acceso a los datos CMIP6

Los datos de los diferentes modelos se encuentran disponibles en la plataforma en la nube de `Google Storage` en formato [`Zarr`](https://zarr.readthedocs.io/en/stable/). Para acceder a los datos de los diferentes escenarios de cambio climático podemos usar la libreria [`xmip`](https://cmip6-preprocessing.readthedocs.io/en/latest/?badge=latest). Para crear una conexión con el repositorio de datos de Google usaremos el método [`google_cmip_col`](https://cmip6-preprocessing.readthedocs.io/en/latest/_modules/xmip/utils.html#google_cmip_col:~:text=def%20google_cmip_col(catalog%3D%22main%22)%3A) que nos permite acceder a los datos de [`Pangeo`](https://pangeo.io/) a través de [`intake`](https://intake.readthedocs.io/en/latest/). 

In [2]:
cat = google_cmip_col()
cat

Como podemos ver hay una gran cantidad de modelaciones de mas de 30 instituciones alrededor del mundo. 

In [3]:
query = dict(
    source_id = [
     'IPSL-CM6A-LR',
     'MPI-ESM1-2-LR',
     'GFDL-ESM4',
     'EC-Earth3',
     'CMCC-ESM2',
     'CESM2',
    ],
    experiment_id = ['historical','ssp126', 'ssp370', 'ssp245', 'ssp585'],
    grid_label='gn',
)
cat_filt = cat.search(
    **query,
    variable_id='tos',
    member_id=['r1i1p1f1',],#'r2i1p1f1'
    table_id='Omon'
)
kwargs = dict(preprocess=combined_preprocessing, xarray_open_kwargs=dict(use_cftime=True), aggregate=False)
ddict = cat_filt.to_dataset_dict(**kwargs)


--> The keys in the returned dictionary of datasets are constructed as follows:
	'activity_id.institution_id.source_id.experiment_id.member_id.table_id.variable_id.grid_label.zstore.dcpp_init_year.version'


Podemos ver cada una de las llaves de este diccionario de la siguiente manera

`Xarray.Dataset` no soporta tener multiples `Datasets`  anidados en un solo objeto de `Xarray`. Sin embargo podemos crear un objeto llamado [`Xarray.datatree`](https://xarray-datatree.readthedocs.io/en/latest/quick-overview.html) que nos permite poner todos nuestros `Datasets` en un solo objeto de manerar herarquica. Para entender un poco mas los formatos y objeto de tipo herarquico vea este [ejemplo](https://xarray-datatree.readthedocs.io/en/latest/hierarchical-data.html)

Para acceder a los datos dentro de este `Xarray.datatree` usamos notación de diccionarios de `Python`

Los datos provenientes del modelo CESM2 tiene `cftime.DatetimeNoLeap` como formato de fecha. Normalmente `Xarray` funciona con estampas de tiempo en formato `datetime`. Para evitar errores más adelante procedemeremos a reemplazar este formato.  

Con los datos en un solo objeto de `Xarray` podemos calcular la temperatura media global para cada uno de los modelos independientemente utilizando el metodo `.mean()`

## 2. Temperatura media global ponderada

## Temperatura Media Global de la Superficie del Mar

In [4]:
cat_area = cat.search(
    **query,
    table_id='Ofx',
    variable_id='areacello',
)
ddict_area = cat_area.to_dataset_dict(**kwargs)


--> The keys in the returned dictionary of datasets are constructed as follows:
	'activity_id.institution_id.source_id.experiment_id.member_id.table_id.variable_id.grid_label.zstore.dcpp_init_year.version'


In [5]:
from xmip.postprocessing import match_metrics
ddict_w_area = match_metrics(ddict, ddict_area, 'areacello', print_statistics=True) 

Processed 26 datasets.
Exact matches:{'areacello': 0}
Other matches:{'areacello': 26}
No match found:{'areacello': 0}


In [6]:
from xmip.postprocessing import concat_members

ddict_trimmed = {k:ds.sel(time=slice(None, '2100')) for k,ds in ddict_w_area.items()}
ddict_combined_members = concat_members(
    ddict_w_area,
    concat_kwargs = {'coords':'minimal', 'compat':'override', 'join':'override'}
)

In [7]:
from datatree import DataTree

# create a path: dataset dictionary, where the path is based on each datasets attributes
tree_dict = {f"{ds.source_id}/{ds.experiment_id}/":ds for ds in ddict_combined_members.values()}

dt = DataTree.from_dict(tree_dict)
dt

DataTree('None', parent=None)
├── DataTree('CMCC-ESM2')
│   ├── DataTree('ssp126')
│   │       Dimensions:         (member_id: 1, dcpp_init_year: 1, time: 1032, x: 292,
│   │                            y: 362, vertex: 4, bnds: 2)
│   │       Coordinates: (12/13)
│   │           lat             (x, y) float64 dask.array<chunksize=(292, 362), meta=np.ndarray>
│   │           lon             (x, y) float64 dask.array<chunksize=(292, 362), meta=np.ndarray>
│   │         * time            (time) object 2015-01-16 12:00:00 ... 2100-12-16 12:00:00
│   │           lat_verticies   (x, y, vertex) float64 dask.array<chunksize=(292, 362, 4), meta=np.ndarray>
│   │           lon_verticies   (x, y, vertex) float64 dask.array<chunksize=(292, 362, 4), meta=np.ndarray>
│   │           time_bounds     (time, bnds) object dask.array<chunksize=(1032, 2), meta=np.ndarray>
│   │           ...              ...
│   │         * y               (y) int64 0 1 2 3 4 5 6 7 ... 355 356 357 358 359 360 361
│   │           lon_bounds      (bnds, x, y) float64 dask.array<chunksize=(1, 292, 362), meta=np.ndarray>
│   │           lat_bounds      (bnds, x, y) float64 dask.array<chunksize=(1, 292, 362), meta=np.ndarray>
│   │         * member_id       (member_id) object 'r1i1p1f1'
│   │         * dcpp_init_year  (dcpp_init_year) float64 nan
│   │           areacello       (member_id, dcpp_init_year, x, y) float32 dask.array<chunksize=(1, 1, 292, 362), meta=np.ndarray>
│   │       Dimensions without coordinates: vertex, bnds
│   │       Data variables:
│   │           tos             (member_id, dcpp_init_year, time, x, y) float32 dask.array<chunksize=(1, 1, 253, 292, 362), meta=np.ndarray>
│   │       Attributes: (12/64)
│   │           Conventions:                      CF-1.7 CMIP-6.2
│   │           activity_id:                      ScenarioMIP
│   │           branch_method:                    standard
│   │           branch_time_in_child:             60225.0
│   │           branch_time_in_parent:            60225.0
│   │           cmor_version:                     3.6.0
│   │           ...                               ...
│   │           intake_esm_attrs:variable_id:     tos
│   │           intake_esm_attrs:grid_label:      gn
│   │           intake_esm_attrs:zstore:          gs://cmip6/CMIP6/ScenarioMIP/CMCC/CMCC-...
│   │           intake_esm_attrs:version:         20210126
│   │           intake_esm_attrs:_data_format_:   zarr
│   │           intake_esm_dataset_key:           ScenarioMIP.CMCC.CMCC-ESM2.ssp126.r1i1p...
│   ├── DataTree('ssp245')
│   │       Dimensions:         (member_id: 1, dcpp_init_year: 1, time: 1032, x: 292,
│   │                            y: 362, vertex: 4, bnds: 2)
│   │       Coordinates: (12/13)
│   │           lat             (x, y) float64 dask.array<chunksize=(292, 362), meta=np.ndarray>
│   │           lon             (x, y) float64 dask.array<chunksize=(292, 362), meta=np.ndarray>
│   │         * time            (time) object 2015-01-16 12:00:00 ... 2100-12-16 12:00:00
│   │           lat_verticies   (x, y, vertex) float64 dask.array<chunksize=(292, 362, 4), meta=np.ndarray>
│   │           lon_verticies   (x, y, vertex) float64 dask.array<chunksize=(292, 362, 4), meta=np.ndarray>
│   │           time_bounds     (time, bnds) object dask.array<chunksize=(1032, 2), meta=np.ndarray>
│   │           ...              ...
│   │         * y               (y) int64 0 1 2 3 4 5 6 7 ... 355 356 357 358 359 360 361
│   │           lon_bounds      (bnds, x, y) float64 dask.array<chunksize=(1, 292, 362), meta=np.ndarray>
│   │           lat_bounds      (bnds, x, y) float64 dask.array<chunksize=(1, 292, 362), meta=np.ndarray>
│   │         * member_id       (member_id) object 'r1i1p1f1'
│   │         * dcpp_init_year  (dcpp_init_year) float64 nan
│   │           areacello       (member_id, dcpp_init_year, x, y) float32 dask.array<chunksize=(1, 1, 292, 362), meta=np.ndarray>
│   │       Dimensions without coordinates: vertex, bnds
│   │    

In [8]:
dt.nbytes / 1e9  # size in GB

20.910565072

In [9]:
dt_single_member = DataTree()
for model_name, model in dt.children.items():
    member_id_values = []
    for experiment_name, experiment in model.children.items():
        ds = experiment.ds
        member_id_values.append(set(ds.member_id.data))  
    
    # find the intersection of all values
    # print(member_id_values)
    full_members = set(member_id_values[0]).intersection(*member_id_values)
    # sort and take the first one
    pick_member = sorted(full_members)[0]
    dt_single_member[model_name] = model.sel(member_id=pick_member)

In [10]:
from datatree import DataTree

# create a path: dataset dictionary, where the path is based on each datasets attributes
tree_dict = {f"{ds.source_id}/{ds.experiment_id}/":ds for ds in ddict_combined_members.values()}

dt = DataTree.from_dict(tree_dict)
dt

DataTree('None', parent=None)
├── DataTree('CMCC-ESM2')
│   ├── DataTree('ssp126')
│   │       Dimensions:         (member_id: 1, dcpp_init_year: 1, time: 1032, x: 292,
│   │                            y: 362, vertex: 4, bnds: 2)
│   │       Coordinates: (12/13)
│   │           lat             (x, y) float64 dask.array<chunksize=(292, 362), meta=np.ndarray>
│   │           lon             (x, y) float64 dask.array<chunksize=(292, 362), meta=np.ndarray>
│   │         * time            (time) object 2015-01-16 12:00:00 ... 2100-12-16 12:00:00
│   │           lat_verticies   (x, y, vertex) float64 dask.array<chunksize=(292, 362, 4), meta=np.ndarray>
│   │           lon_verticies   (x, y, vertex) float64 dask.array<chunksize=(292, 362, 4), meta=np.ndarray>
│   │           time_bounds     (time, bnds) object dask.array<chunksize=(1032, 2), meta=np.ndarray>
│   │           ...              ...
│   │         * y               (y) int64 0 1 2 3 4 5 6 7 ... 355 356 357 358 359 360 361
│   │           lon_bounds      (bnds, x, y) float64 dask.array<chunksize=(1, 292, 362), meta=np.ndarray>
│   │           lat_bounds      (bnds, x, y) float64 dask.array<chunksize=(1, 292, 362), meta=np.ndarray>
│   │         * member_id       (member_id) object 'r1i1p1f1'
│   │         * dcpp_init_year  (dcpp_init_year) float64 nan
│   │           areacello       (member_id, dcpp_init_year, x, y) float32 dask.array<chunksize=(1, 1, 292, 362), meta=np.ndarray>
│   │       Dimensions without coordinates: vertex, bnds
│   │       Data variables:
│   │           tos             (member_id, dcpp_init_year, time, x, y) float32 dask.array<chunksize=(1, 1, 253, 292, 362), meta=np.ndarray>
│   │       Attributes: (12/64)
│   │           Conventions:                      CF-1.7 CMIP-6.2
│   │           activity_id:                      ScenarioMIP
│   │           branch_method:                    standard
│   │           branch_time_in_child:             60225.0
│   │           branch_time_in_parent:            60225.0
│   │           cmor_version:                     3.6.0
│   │           ...                               ...
│   │           intake_esm_attrs:variable_id:     tos
│   │           intake_esm_attrs:grid_label:      gn
│   │           intake_esm_attrs:zstore:          gs://cmip6/CMIP6/ScenarioMIP/CMCC/CMCC-...
│   │           intake_esm_attrs:version:         20210126
│   │           intake_esm_attrs:_data_format_:   zarr
│   │           intake_esm_dataset_key:           ScenarioMIP.CMCC.CMCC-ESM2.ssp126.r1i1p...
│   ├── DataTree('ssp245')
│   │       Dimensions:         (member_id: 1, dcpp_init_year: 1, time: 1032, x: 292,
│   │                            y: 362, vertex: 4, bnds: 2)
│   │       Coordinates: (12/13)
│   │           lat             (x, y) float64 dask.array<chunksize=(292, 362), meta=np.ndarray>
│   │           lon             (x, y) float64 dask.array<chunksize=(292, 362), meta=np.ndarray>
│   │         * time            (time) object 2015-01-16 12:00:00 ... 2100-12-16 12:00:00
│   │           lat_verticies   (x, y, vertex) float64 dask.array<chunksize=(292, 362, 4), meta=np.ndarray>
│   │           lon_verticies   (x, y, vertex) float64 dask.array<chunksize=(292, 362, 4), meta=np.ndarray>
│   │           time_bounds     (time, bnds) object dask.array<chunksize=(1032, 2), meta=np.ndarray>
│   │           ...              ...
│   │         * y               (y) int64 0 1 2 3 4 5 6 7 ... 355 356 357 358 359 360 361
│   │           lon_bounds      (bnds, x, y) float64 dask.array<chunksize=(1, 292, 362), meta=np.ndarray>
│   │           lat_bounds      (bnds, x, y) float64 dask.array<chunksize=(1, 292, 362), meta=np.ndarray>
│   │         * member_id       (member_id) object 'r1i1p1f1'
│   │         * dcpp_init_year  (dcpp_init_year) float64 nan
│   │           areacello       (member_id, dcpp_init_year, x, y) float32 dask.array<chunksize=(1, 1, 292, 362), meta=np.ndarray>
│   │       Dimensions without coordinates: vertex, bnds
│   │    

In [11]:
for i in dt['/CESM2'].keys():
    dt[f'/CESM2/{i}'] = dt[f'/CESM2/{i}'].assign_coords(time=("time", np.array([np.datetime64(j)
                                                                               for j in
                                                                               dt[f'/CESM2/{i}']['time'].values])))

In [ ]:
# average temperature globally
def global_mean_sst(ds):
    return ds.tos.weighted(ds.areacello.fillna(0)).mean(['x', 'y']).persist() 

timeseries = dt_single_member.map_over_subtree(global_mean_sst)
timeseries

In [ ]:
def get_ref_value(ds):
    return ds.sel(time=slice('1950','1980')).mean('time')

anomaly = DataTree()
for model_name, model in timeseries.children.items():
    # model-specific base period
    base_period = get_ref_value(model["historical"].ds)
    anomaly[model_name] = model - base_period   # subtree - Dataset

In [ ]:
def replace_time(ds):
    start_date = ds.time.data[0]
    new_time = xr.cftime_range(f"{start_date.year}-{start_date.month:02}", freq='1MS', periods=len(ds.time))
    ds_new_cal = ds.assign_coords(time=new_time, source_id=model_name)
    return ds_new_cal
    

experiment_dict = {k:[] for k in ['historical','ssp126', 'ssp370', 'ssp245', 'ssp585']}

for model_name, model in anomaly.children.items():
    for experiment_name, experiment in model.children.items():
        # replace the time dimension
        ds_new_cal = replace_time(experiment.ds)
        experiment_dict[experiment_name].append(ds_new_cal.load())

# concatenate all models for a given experiment
plot_dict = {k:xr.concat(ds_lst, dim='source_id') for k, ds_lst in experiment_dict.items()}

In [ ]:
store = 'https://ncsa.osn.xsede.org/Pangeo/pangeo-forge/HadISST-feedstock/hadisst.zarr'
ds_obs = xr.open_dataset(store, engine='zarr', chunks={}).rename({'sst':'tos'}).convert_calendar('standard', use_cftime=True)

# mask missing values
ds_obs = ds_obs.where(abs(ds_obs.tos)<50)

# reconstruct area
area = np.cos(np.deg2rad(ds_obs.latitude)) * 110e3 **2

# Repeat same steps from above
ds_obs_ts = ds_obs.weighted(area).mean(['longitude', 'latitude'])
ds_obs_anomaly = ds_obs_ts - get_ref_value(ds_obs_ts)

# add to plot_dict
plot_dict['observations'] = ds_obs_anomaly.expand_dims(['source_id', 'dcpp_init_year']).load()

In [ ]:
fig, ax = plt.subplots()

color_dict = {
    'historical':'0.5',
    'ssp126': 'C2',
    'ssp245': 'gold',
    'ssp370': 'C1',
    'ssp585': 'C3',
    'observations': 'C5'
}
for experiment, ds in plot_dict.items():
    ds = ds.assign_coords(time=('time', ds.time.data.astype("datetime64[ns]")))
    color = color_dict[experiment]
    smooth = ds['tos'].sel(time=slice(None, '2100')).rolling(time=2*12).mean().squeeze('dcpp_init_year')
    lw = 2 if experiment=='observations' else 1.5
    shaded_line_plot(smooth, 'source_id', ax=ax, spreads=[2.0], alphas=[0.2], line_kwargs=dict(color=color, label=f"{experiment} ({len(ds.source_id)})", lw=lw))
plt.legend(loc=2);
plt.grid()
plt.tight_layout()

---

## Resumen final
En este cuadernillo (notebook) revisamos temas relacionados con el acceso a la informacion proveniente de diferentes escenarios de Cambio Climático .....


## Fuentes y referencias
Finally, be rigorous in your citations and references as necessary. Give credit where credit is due. Also, feel free to link to relevant external material, further reading, documentation, etc. Then you're done! Give yourself a quick review, a high five, and send us a pull request. A few final notes:
 - `Kernel > Restart Kernel and Run All Cells...` to confirm that your notebook will cleanly run from start to finish
 - `Kernel > Restart Kernel and Clear All Outputs...` before committing your notebook, our machines will do the heavy lifting
 - Take credit! Provide author contact information if you'd like; if so, consider adding information here at the bottom of your notebook
 - Give credit! Attribute appropriate authorship for referenced code, information, images, etc.
 - Only include what you're legally allowed: **no copyright infringement or plagiarism**
 
Thank you for your contribution!